# Labelling Dataset Ajaib

### 1. Copy Data Clean dan Simpan di Collection Baru

In [1]:
from pymongo import MongoClient

# Membuat koneksi ke database MongoDB
client = MongoClient('localhost', 27017)
db = client['google_play_store_data']  
clean_collection = db['03. clean_data_ajaib'] 
label_collection = db['04. label_data_ajaib'] 

# Mendapatkan data dari clean_collection
data = clean_collection.find({}) 
data_list = list(data)
label_collection.insert_many(data_list)

InsertManyResult([ObjectId('663862c1dd520c9ba22efdc2'), ObjectId('663862c1dd520c9ba22efdc3'), ObjectId('663862c1dd520c9ba22efdc4'), ObjectId('663862c1dd520c9ba22efdc5'), ObjectId('663862c1dd520c9ba22efdc6'), ObjectId('663862c1dd520c9ba22efdc7'), ObjectId('663862c1dd520c9ba22efdc8'), ObjectId('663862c1dd520c9ba22efdc9'), ObjectId('663862c1dd520c9ba22efdca'), ObjectId('663862c1dd520c9ba22efdcc'), ObjectId('663862c1dd520c9ba22efdcd'), ObjectId('663862c1dd520c9ba22efdce'), ObjectId('663862c1dd520c9ba22efdcf'), ObjectId('663862c1dd520c9ba22efdd0'), ObjectId('663862c1dd520c9ba22efdd1'), ObjectId('663862c1dd520c9ba22efdd2'), ObjectId('663862c1dd520c9ba22efdd3'), ObjectId('663862c1dd520c9ba22efdd4'), ObjectId('663862c1dd520c9ba22efdd5'), ObjectId('663862c1dd520c9ba22efdd6'), ObjectId('663862c1dd520c9ba22efdd7'), ObjectId('663862c1dd520c9ba22efdd8'), ObjectId('663862c1dd520c9ba22efdd9'), ObjectId('663862c1dd520c9ba22efddb'), ObjectId('663862c1dd520c9ba22efddc'), ObjectId('663862c1dd520c9ba22efd

### 2. Memberikan label 2 untuk dataset yang memiliki content **bagus|recomended|mantap**

In [2]:
import re

# Koneksi ke MongoDB
client = MongoClient('localhost', 27017)  
db = client['google_play_store_data']   
label_collection = db['04. label_data_ajaib']  

# Mendapatkan dokumen dengan data_clean mengandung kata bagus|recomended|mantap
documents = label_collection.find({'data_clean': {'$regex': re.compile(r'bagus|recomended|mantap', re.IGNORECASE)}})

# Update field 'label' menjadi 2 untuk dokumen yang memenuhi kriteria
for document in documents:
    label_collection.update_one({'_id': document['_id']}, {'$set': {'label': 2}})

print("Proses update selesai.")

Proses update selesai.


### 3. Memberikan label 1 untuk dataset yang memiliki content **jelek|buruk|gagal|error|ribet|scam|kecewa|susah|parah|lambat**

In [3]:
from pymongo import MongoClient
import re

# Koneksi ke MongoDB
client = MongoClient('localhost', 27017) 
db = client['google_play_store_data']   
label_collection = db['04. label_data_ajaib']  

# Mendapatkan dokumen dengan data_clean mengandung kata jelek|buruk|gagal|error|ribet|scam|kecewa|susah|parah|lambat
documents = label_collection.find({'data_clean': {'$regex': re.compile(r'jelek|buruk|gagal|error|ribet|scam|kecewa|susah|parah|lambat', re.IGNORECASE)}})

# Update field 'label' menjadi 1 untuk dokumen yang memenuhi kriteria
for document in documents:
    label_collection.update_one({'_id': document['_id']}, {'$set': {'label': 1}})

print("Proses update selesai.")


Proses update selesai.


### 4. Memberikan label 0 untuk dataset yang memiliki content kategori netral yang dilakukan manual

### 5. Cek Jumlah Masing-Masing Kategori

In [4]:
from pymongo import MongoClient

# Membuat koneksi ke database MongoDB
client = MongoClient('localhost', 27017)
db = client['google_play_store_data']  
label_collection = db['04. label_data_ajaib'] 

# Melakukan agregasi untuk menjumlahkan jumlah label positif (2), negatif (1), dan netral (0)
pipeline = [
    {"$group": {"_id": "$label", "count": {"$sum": 1}}}
]

# Melakukan agregasi dan mendapatkan hasilnya
results = label_collection.aggregate(pipeline)

# Menampilkan hasil agregasi
for result in results:
    print(result['_id'], result['count'])


None 5641
1 2020
2 943


### 6. Mengubah limit masing-masing label menjadi 500 saja dan sisanya diganti None

In [5]:
from pymongo import MongoClient

# Koneksi ke database MongoDB
client = MongoClient('localhost', 27017)
db = client['google_play_store_data']  
label_collection = db['04. label_data_ajaib']

# Jumlah maksimum entri yang akan disimpan untuk setiap label
limit_per_label = 500

# Memperoleh 500 data pertama dari kategori positif
positive_documents = label_collection.find({"label": 2}).limit(limit_per_label)

# Memperbarui label dari entri yang tersisa menjadi None
label_collection.update_many({"label": 2, "_id": {"$nin": [doc["_id"] for doc in positive_documents]}}, {"$set": {"label": None}})

# Output informasi tentang perubahan
print("Perubahan label telah dilakukan.")

Perubahan label telah dilakukan.


In [6]:
from pymongo import MongoClient

# Koneksi ke database MongoDB
client = MongoClient('localhost', 27017)
db = client['google_play_store_data']  
label_collection = db['04. label_data_ajaib']

# Jumlah maksimum entri yang akan disimpan untuk setiap label
limit_per_label = 500

# Memperoleh 500 data pertama dari kategori positif
negative_documents = label_collection.find({"label": 1}).limit(limit_per_label)

# Memperbarui label dari entri yang tersisa menjadi None
label_collection.update_many({"label": 1, "_id": {"$nin": [doc["_id"] for doc in negative_documents]}}, {"$set": {"label": None}})

# Output informasi tentang perubahan
print("Perubahan label telah dilakukan.")

Perubahan label telah dilakukan.


In [7]:
from pymongo import MongoClient

# Membuat koneksi ke database MongoDB
client = MongoClient('localhost', 27017)
db = client['google_play_store_data']  
label_collection = db['04. label_data_ajaib'] 

# Melakukan agregasi untuk menjumlahkan jumlah label positif (2), negatif (1), dan netral (0)
pipeline = [
    {"$group": {"_id": "$label", "count": {"$sum": 1}}}
]

# Melakukan agregasi dan mendapatkan hasilnya
results = label_collection.aggregate(pipeline)

# Menampilkan hasil agregasi
for result in results:
    print(result['_id'], result['count'])


None 7604
1 500
2 500


# Labelling Dataset Bibit

### 1. Copy Data Clean dan Simpan di Collection Baru

In [8]:
from pymongo import MongoClient

# Membuat koneksi ke database MongoDB
client = MongoClient('localhost', 27017)
db = client['google_play_store_data']  
clean_collection = db['03. clean_data_bibit'] 
label_collection = db['04. label_data_bibit'] 

# Mendapatkan data dari clean_collection
data = clean_collection.find({}) 
data_list = list(data)
label_collection.insert_many(data_list)

InsertManyResult([ObjectId('6638614cdd520c9ba22ee66c'), ObjectId('6638614cdd520c9ba22ee66d'), ObjectId('6638614cdd520c9ba22ee66e'), ObjectId('6638614cdd520c9ba22ee66f'), ObjectId('6638614cdd520c9ba22ee670'), ObjectId('6638614cdd520c9ba22ee671'), ObjectId('6638614cdd520c9ba22ee672'), ObjectId('6638614cdd520c9ba22ee673'), ObjectId('6638614cdd520c9ba22ee674'), ObjectId('6638614cdd520c9ba22ee675'), ObjectId('6638614cdd520c9ba22ee676'), ObjectId('6638614cdd520c9ba22ee677'), ObjectId('6638614cdd520c9ba22ee678'), ObjectId('6638614cdd520c9ba22ee679'), ObjectId('6638614cdd520c9ba22ee67a'), ObjectId('6638614cdd520c9ba22ee67b'), ObjectId('6638614cdd520c9ba22ee67c'), ObjectId('6638614cdd520c9ba22ee67d'), ObjectId('6638614cdd520c9ba22ee67e'), ObjectId('6638614cdd520c9ba22ee67f'), ObjectId('6638614cdd520c9ba22ee680'), ObjectId('6638614cdd520c9ba22ee681'), ObjectId('6638614cdd520c9ba22ee682'), ObjectId('6638614cdd520c9ba22ee683'), ObjectId('6638614cdd520c9ba22ee684'), ObjectId('6638614cdd520c9ba22ee6

### 2. Memberikan label 2 untuk dataset yang memiliki content **bagus|recomended|mantap**

In [9]:
import re

# Koneksi ke MongoDB
client = MongoClient('localhost', 27017)  
db = client['google_play_store_data']   
label_collection = db['04. label_data_bibit']  

# Mendapatkan dokumen dengan data_clean mengandung kata bagus|recomended|mantap
documents = label_collection.find({'data_clean': {'$regex': re.compile(r'bagus|recomended|mantap', re.IGNORECASE)}})

# Update field 'label' menjadi 2 untuk dokumen yang memenuhi kriteria
for document in documents:
    label_collection.update_one({'_id': document['_id']}, {'$set': {'label': 2}})

print("Proses update selesai.")

Proses update selesai.


### 3. Memberikan label 1 untuk dataset yang memiliki content **jelek|buruk|gagal|error|ribet|scam|kecewa|susah|parah|lambat**


In [10]:
from pymongo import MongoClient
import re

# Koneksi ke MongoDB
client = MongoClient('localhost', 27017) 
db = client['google_play_store_data']   
label_collection = db['04. label_data_bibit']  

# Mendapatkan dokumen dengan data_clean mengandung kata jelek|buruk|gagal|error|ribet|scam|kecewa|susah|parah|lambat
documents = label_collection.find({'data_clean': {'$regex': re.compile(r'jelek|buruk|gagal|error|ribet|scam|kecewa|susah|parah|lambat', re.IGNORECASE)}})

# Update field 'label' menjadi 1 untuk dokumen yang memenuhi kriteria
for document in documents:
    label_collection.update_one({'_id': document['_id']}, {'$set': {'label': 1}})

print("Proses update selesai.")

Proses update selesai.
{'_id': ObjectId('6638614cdd520c9ba22ee66c'), 'at': datetime.datetime(2024, 5, 5, 10, 54, 32), 'tokenized_content': ['mau', 'daftar', 'saja', 'di', 'persulit', 'dari', 'bulan', 'april', 'gagal', 'melulu', 'daftar', 'pertama', 'foto', 'diri', 'sama', 'ktp', 'status', 'gagal', 'perbaikan', 'foto', 'diri', 'sama', 'sim', 'kembali', 'lagi', 'gagal', 'perbaikan', 'kembali', 'foto', 'diri', 'sama', 'sim', 'ktp', 'kembali', 'lagi', 'gagal', 'tanya', 'admin', 'idak', 'membantu', 'jadi', 'males'], 'filtered_content': ['daftar', 'persulit', 'april', 'gagal', 'melulu', 'daftar', 'foto', 'ktp', 'status', 'gagal', 'perbaikan', 'foto', 'sim', 'gagal', 'perbaikan', 'foto', 'sim', 'ktp', 'gagal', 'admin', 'idak', 'membantu', 'males'], 'data_clean': 'daftar sulit april gagal melulu daftar foto ktp status gagal baik foto sim gagal baik foto sim ktp gagal admin idak bantu males', 'label': 1}
{'_id': ObjectId('6638614cdd520c9ba22ee66d'), 'at': datetime.datetime(2024, 5, 3, 17, 16, 4

### 4. Memberikan label 0 untuk dataset yang memiliki content kategori netral yang dilakukan manual

### 5. Cek Jumlah Masing-Masing Kategori

In [11]:
from pymongo import MongoClient

# Membuat koneksi ke database MongoDB
client = MongoClient('localhost', 27017)
db = client['google_play_store_data']  
label_collection = db['04. label_data_bibit']  

# Melakukan agregasi untuk menjumlahkan jumlah label positif (2), negatif (1), dan netral (0)
pipeline = [
    {"$group": {"_id": "$label", "count": {"$sum": 1}}}
]

# Melakukan agregasi dan mendapatkan hasilnya
results = label_collection.aggregate(pipeline)

# Menampilkan hasil agregasi
for result in results:
    print(result['_id'], result['count'])


None 5979
1 1346
2 910


### 6. Mengubah limit masing-masing label menjadi 500 saja dan sisanya diganti None

In [12]:
from pymongo import MongoClient

# Koneksi ke database MongoDB
client = MongoClient('localhost', 27017)
db = client['google_play_store_data']  
label_collection = db['04. label_data_bibit']  

# Jumlah maksimum entri yang akan disimpan untuk setiap label
limit_per_label = 500

# Memperoleh 500 data pertama dari kategori positif
positive_documents = label_collection.find({"label": 2}).limit(limit_per_label)

# Memperbarui label dari entri yang tersisa menjadi None
label_collection.update_many({"label": 2, "_id": {"$nin": [doc["_id"] for doc in positive_documents]}}, {"$set": {"label": None}})

# Output informasi tentang perubahan
print("Perubahan label telah dilakukan.")

Perubahan label telah dilakukan.


In [13]:
from pymongo import MongoClient

# Koneksi ke database MongoDB
client = MongoClient('localhost', 27017)
db = client['google_play_store_data']  
label_collection = db['04. label_data_bibit']  

# Jumlah maksimum entri yang akan disimpan untuk setiap label
limit_per_label = 500

# Memperoleh 500 data pertama dari kategori positif
negative_documents = label_collection.find({"label": 1}).limit(limit_per_label)

# Memperbarui label dari entri yang tersisa menjadi None
label_collection.update_many({"label": 1, "_id": {"$nin": [doc["_id"] for doc in negative_documents]}}, {"$set": {"label": None}})

# Output informasi tentang perubahan
print("Perubahan label telah dilakukan.")

Perubahan label telah dilakukan.


In [14]:
from pymongo import MongoClient

# Membuat koneksi ke database MongoDB
client = MongoClient('localhost', 27017)
db = client['google_play_store_data']  
label_collection = db['04. label_data_bibit']  

# Melakukan agregasi untuk menjumlahkan jumlah label positif (2), negatif (1), dan netral (0)
pipeline = [
    {"$group": {"_id": "$label", "count": {"$sum": 1}}}
]

# Melakukan agregasi dan mendapatkan hasilnya
results = label_collection.aggregate(pipeline)

# Menampilkan hasil agregasi
for result in results:
    print(result['_id'], result['count'])


None 7235
1 500
2 500
